In [1]:
import random
import time
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.animation as animation
%matplotlib inline


In [2]:
def bubble_sort(arr):
    a = arr.copy()
    states = [a.copy()]
    swap_count = 0
    n = len(a)
    for i in range(n):
        for j in range(0, n - i - 1):
            if a[j] > a[j + 1]:
                a[j], a[j + 1] = a[j + 1], a[j]
                swap_count += 1
                states.append(a.copy())
    return a, swap_count, states

def quick_sort(arr):
    a = arr.copy()
    states = [a.copy()]
    swap_count = 0

    def _quick_sort(low, high):
        nonlocal swap_count
        if low < high:
            p = partition(low, high)
            _quick_sort(low, p - 1)
            _quick_sort(p + 1, high)

    def partition(low, high):
        nonlocal swap_count
        pivot = a[high]
        i = low
        for j in range(low, high):
            if a[j] < pivot:
                a[i], a[j] = a[j], a[i]
                swap_count += 1
                states.append(a.copy())
                i += 1
        a[i], a[high] = a[high], a[i]
        swap_count += 1
        states.append(a.copy())
        return i

    _quick_sort(0, len(a) - 1)
    return a, swap_count, states

def heap_sort(arr):
    a = arr.copy()
    n = len(a)
    states = [a.copy()]
    swap_count = 0

    def heapify(n, i):
        nonlocal swap_count
        largest = i
        left = 2 * i + 1
        right = 2 * i + 2

        if left < n and a[left] > a[largest]:
            largest = left
        if right < n and a[right] > a[largest]:
            largest = right
        if largest != i:
            a[i], a[largest] = a[largest], a[i]
            swap_count += 1
            states.append(a.copy())
            heapify(n, largest)

    # Build max heap.
    for i in range(n // 2 - 1, -1, -1):
        heapify(n, i)

    # Extract elements one by one.
    for i in range(n - 1, 0, -1):
        a[i], a[0] = a[0], a[i]
        swap_count += 1
        states.append(a.copy())
        heapify(i, 0)

    return a, swap_count, states


In [3]:
def animate_sort(states, title):
    fig, ax = plt.subplots()
    bars = ax.bar(range(len(states[0])), states[0], align="edge", color='skyblue')
    ax.set_title(title)
    ax.set_xlim(0, len(states[0]))
    ax.set_ylim(0, max(states[0]) * 1.1)
    text = ax.text(0.02, 0.95, "", transform=ax.transAxes)

    def update(frame):
        for bar, val in zip(bars, states[frame]):
            bar.set_height(val)
        text.set_text(f"Step: {frame}/{len(states)-1}")
        return bars, text

    ani = animation.FuncAnimation(fig, update, frames=range(len(states)), interval=200, repeat=False)
    plt.close(fig)  # Prevents duplicate static image in some environments.
    return ani



In [4]:
# Example usage for a single sort:
sample_array = random.sample(range(1, 21), 20)
_, swaps, bubble_states = bubble_sort(sample_array)
ani_bubble = animate_sort(bubble_states, f"Bubble Sort (Swaps: {swaps})")
from IPython.display import HTML
HTML(ani_bubble.to_jshtml())


In [5]:

_, swaps, quick_sort_states = quick_sort(sample_array)
ani_quick_sort = animate_sort(quick_sort_states, f"quick Sort (Swaps: {swaps})")
from IPython.display import HTML
HTML(ani_quick_sort.to_jshtml())


In [6]:

_, swaps, heap_sort_states = heap_sort(sample_array)
ani_heap_sort = animate_sort(heap_sort_states, f"heap_sort (Swaps: {swaps})")
from IPython.display import HTML
HTML(ani_heap_sort.to_jshtml())


In [8]:
def benchmark_sorting(n, trials=15):
    results = {"Algorithm": [], "Average Swaps": [], "Average Time (ms)": []}
    algorithms = [
        ("BubbleSort", bubble_sort),
        ("QuickSort", quick_sort),
        ("HeapSort", heap_sort)
    ]
    for name, sort_func in algorithms:
        total_swaps = 0
        total_time = 0
        for _ in range(trials):
            arr = random.sample(range(1, n + 1), n)
            start = time.time()
            _, swaps, _ = sort_func(arr)
            end = time.time()
            total_swaps += swaps
            total_time += (end - start)
        results["Algorithm"].append(name)
        results["Average Swaps"].append(total_swaps / trials)
        results["Average Time (ms)"].append((total_time / trials) * 1000)

    return pd.DataFrame(results)

# Run benchmarks on, for example, arrays of 1000 elements.
df_benchmark = benchmark_sorting(1000, trials=15)
df_benchmark


Algorithm  Average Swaps  Average Time (ms)
0  BubbleSort  248078.866667        7935.429970
1   QuickSort    5918.800000         153.184048
2    HeapSort    9078.533333         252.529240